# Practical work on SAR statistics

### Emanuele DALSASSO, Florence TUPIN

Images of the practical work can be found on: 
https://perso.telecom-paristech.fr/dalsasso/TPSAR/
and 
https://perso.telecom-paristech.fr/tupin/TPSAR/DATA/images/

Codes of the practical work are available here:
https://perso.telecom-paristech.fr/dalsasso/TPSAR/

Some useful functions are available in the file *mvalab.py*. 

### Reading of images with TélécomParisTech format
A useful function to read the images with Télécom-Paristech format is *imz2mat*

### Vizualisation of an image 

The function to display a SAR image with an adapted thresholding of the values is 
*visusar*. the first argument containing the image is compulsary, and the second one is 
optional and corresponds to a threshold for the display. 
The value $\alpha$ defines the threshold in this way :

${\rm thres} \:\:=\:\: {\rm vmean} \:\: + \:\: \alpha \: {\rm std}$


vmean is the mean value and std the standard deviation computed on the whole image. Every pixel whose value is above this threshold is displayed with the maximal value.  

When $\alpha$ is 0, the image is displayed with the full dynamic range.
A usual value to display SAR images is 3. 

### Study of homogeneous areas

You have at your disposal a set of images coming from different sensors and with different characteristics on the same area of Flevoland in Netherlands (for each sensor and acquisition mode, an homogeneous area of sea has been selected with *mer* extension, and an area of farmland with  *centre* extension):
- Sentinel-1 sensor (ESA), SLC (Single look Complex) data and GRD (Ground Range Detected) data ;
- ERS sensor (ESA), PRI product (ground range data);
- Alos sensor (JAXA), SLC (Single look Complex) data.

Using an SLC data, check that the sea area follows the distributions given during the course for fully developped speckle by computing the histograms (for phase, real part, imaginary part, intensity and amplitude data). Compute the values of the first moments and the coefficient of variation and comment their values.   

In [0]:
import math
import numpy as npy
import matplotlib.pyplot as plt
import scipy
from scipy import signal

import numpy



#tagnotebook=1
#mvalab.notebook(tagnotebook)



In [0]:
from google_drive_downloader import GoogleDriveDownloader as gdd

gdd.download_file_from_google_drive(file_id='1bc4u2uZy6FfrsKa5fMmUkmMLqEr-0qqt',
                                    dest_path='./librairies.zip',
                                    unzip=True)

In [0]:
import sys
sys.path.append('./librairies/')
import mvalabV2 as mvalab

### 1. Interpretation
Plot the image of Paris and try to see the effect of geometric distortions (layover, shadowing, foreshortening) in the image

In [0]:
repertoire='https://perso.telecom-paristech.fr/dalsasso/TPSAR/paris/'
image = "Eiffel.CXF"
tabimage=mvalab.imz2mat(repertoire+image)
ncol=tabimage[1]
nlig=tabimage[2]
tabimage_ = tabimage[0]

plt.rcParams['figure.figsize'] = [9, 9]
mvalab.visusar(tabimage_)

# histogram of values
plt.figure()
plt.hist(npy.abs(tabimage_.ravel()),bins='auto',normed=True, range=[0.,512])  # 512 sera la valeur max
plt.show()

In [0]:
pageweb="https://perso.telecom-paristech.fr/dalsasso/TPSAR/pilelely/"
image = "Lely.CXF"
im_slc_senti_lely_liste=mvalab.imz2mat(pageweb+image)
im_slc_senti_lely = im_slc_senti_lely_liste[0]
ncol=im_slc_senti_lely_liste[1]
nlig=im_slc_senti_lely_liste[2]

plt.rcParams['figure.figsize'] = [9, 9]
mvalab.visusar(im_slc_senti_lely)

#%%


amp_slc_senti_lely=numpy.abs(im_slc_senti_lely);
int_slc_senti_lely=numpy.multiply(amp_slc_senti_lely,amp_slc_senti_lely);
ph_slc_senti_lely=numpy.angle(im_slc_senti_lely);
real_slc_senti_lely=numpy.real(im_slc_senti_lely);
imag_slc_senti_lely=numpy.imag(im_slc_senti_lely);

plt.hist(amp_slc_senti_lely.ravel(),bins='auto',normed=True,range=[0.,512])  # 512 sera la valeur max. Rayleigh distributed
plt.show()  

# Use the estimated amplitude image to compute the coefficient of variation, being the ratio between the standard variation
# and the mean value of the image
m_A=
sigma_A=
coeff_var_A=

In [0]:
plt.hist(int_slc_senti_lely.ravel(),bins='auto',normed=True,range=[0.,40000])  # Exponential distribution
plt.title('histogram of intensity')
plt.show()
plt.hist(ph_slc_senti_lely.ravel(),bins='auto',normed=True,range=[-npy.pi,npy.pi])  # Uniform distribution
plt.title('histogram of phase')
plt.show()
plt.hist(real_slc_senti_lely.ravel(),bins='auto',normed=True,range=[-300,300])  # Gaussian distribution
plt.title('histogram of real part')
plt.show()
plt.hist(imag_slc_senti_lely.ravel(),bins='auto',normed=True,range=[-300,300])  # Gaussian distribution
plt.title('histogram of imaginary part')
plt.show()



### Multi-looking of data
A common way to reduce the speckle is to multi-look the data.

Compute a multi-look down-sampled image of Lely SLC data using a factor of 1 in the vertical direction and 4 in horizontal (this will give almost square pixels).

Comment the effect of multi-looking. 

Multilooking is computed both in intensity and in amplitude format. Can you see the differences?

In [0]:
masque_vert=numpy.ones((1,4))/4
sentinel_ml_int=signal.convolve2d(numpy.multiply(im_slc_senti_lely, numpy.conj(im_slc_senti_lely)), masque_vert,mode='same')
mvalab.visusar(numpy.sqrt(sentinel_ml_int[:,::4])) 
plt.suptitle(u'SENTINEL : Multivue en intensité')

#% multi-look in amplitude 
plt.figure()
sentinel_ml_amp=signal.convolve2d(npy.abs(im_slc_senti_lely), masque_vert,mode='same')

mvalab.visusar(sentinel_ml_amp[:,::4])   
plt.suptitle(u'SENTINEL : Multivue en amplitude')
#%%


### Multi-looking

A common way to reduce the speckle is to multi-look the data.

In [0]:
pageweb='https://perso.telecom-paristech.fr/tupin/TPSAR/DATA/images/'
image='SentinelGRD_flevoland_centre.imw'
plt.figure()
im_sentigrd_centre=mvalab.imz2mat(pageweb+image)
mvalab.visusar(numpy.abs(im_sentigrd_centre[0])) # mode Z : le plt.figure et le plt.show ne seront pas effectués
plt.suptitle(u'Sentinel-1 GRD')
#plt.figure()


image='SentinelSLC_flevoland_centre.cxs'
im_sentislc_centre=mvalab.imz2mat(pageweb+image)
plt.rcParams['figure.figsize'] = [15, 15]
mvalab.visusar(numpy.abs(im_sentislc_centre[0])) # mode Z : le plt.figure et le plt.show ne seront pas effectués

#do the multilooking downsampled using an horizontal factor of 4 and a vertical one of 1 on the intensity image. 
#Take inspiration from the example above
masque_vert=
sentinel_ml_int=
mvalab.visusar(numpy.sqrt(sentinel_ml_int[::,::4])) 
plt.suptitle(u'SENTINEL : Multivue en intensité')

#% multi-look in amplitude: with the defined mask, apply multilooking in amplitude format 
plt.figure()
sentinel_ml_amp=
mvalab.visusar(sentinel_ml_amp[::,::4])   
plt.suptitle(u'SENTINEL : Multivue en amplitude')
#%%





#### Computation of the Equivalent Number of looks
Use the value of the coefficient of variation to find the number of looks of the Sentinel GRD and ERS data. 
The formula is :
- $\gamma_I=\frac{1}{\sqrt{L}}$ for intensity data 
- $\gamma_A=\frac{0.523}{\sqrt{L}}$

Comment the number of looks you have found for GRD and ERS data.

In [0]:
image='SentinelGRD_flevoland_mer.imw'
im_sentigrd_mer=mvalab.imz2mat(pageweb+image)
mvalab.visusar(numpy.abs(im_sentigrd_mer[0]))
coeff_var_grd = numpy.std(numpy.abs(im_sentigrd_mer[0]))/numpy.mean(numpy.abs(im_sentigrd_mer[0]))
L_grd = numpy.square(0.523/coeff_var_grd)
print('--- coeff var and L ---')
print(coeff_var_grd)
print(L_grd)

image='SentinelSLC_flevoland_mer.cxs'
im_sentislc_mer=mvalab.imz2mat(pageweb+image)
mvalab.visusar(numpy.abs(im_sentislc_mer[0]))
coeff_var_grd = numpy.std(numpy.abs(im_sentislc_mer[0]))/numpy.mean(numpy.abs(im_sentislc_mer[0]))
L_grd = numpy.square(0.523/coeff_var_grd)
print('--- coeff var and L ---')
print(coeff_var_grd)
print(L_grd)

image='ERS_flevoland_mer.imw'
im_ers_mer=mvalab.imz2mat(pageweb+image)
mvalab.visusar(numpy.abs(im_ers_mer[0]))
coeff_var_grd = numpy.std(numpy.abs(im_ers_mer[0]))/numpy.mean(numpy.abs(im_ers_mer[0]))
L_grd = numpy.square(0.523/coeff_var_grd)
print('--- coeff var and L ---')
print(coeff_var_grd)
print(L_grd)

## Coefficient of variation

This coefficient (ratio between standard deviation by mean) is an indication of the local homogeneity of the scene. 


Using 2D convolution to speed up the processing, compute the images of coefficient of variation. Comment the results (which structures of the image are highlighted ?) and the influence of the window size.  


In [0]:
#image='SentinelSLC_flevoland_centre.cxs'
#image='Alos_flevoland_centre.cxf'
image='ERS_flevoland_centre.imw'
#image='ERS_flevoland_mer.imw'


im_slc_senti_centre=mvalab.imz2mat(pageweb+image)
ima_int=numpy.multiply(im_slc_senti_centre[0], numpy.conj(im_slc_senti_centre[0]))

size_window=11;
masque_loc=numpy.ones((size_window,size_window))/(size_window*size_window)
ima_intcarre=numpy.multiply(ima_int,ima_int)

ima_int_mean=signal.convolve2d(ima_int, masque_loc,mode='same')
plt.figure(1);
mvalab.visusar(numpy.sqrt(ima_int));

plt.figure(2);
mvalab.visusar(numpy.sqrt(ima_int_mean));

# COMPUTE THE COEFFICIENT OF VARIATION AS THE RATIO BETWEEN THE STD IMAGE AND THE MEAN IMAGE
ima_int_mean_carre=
ima_variance=
ima_coeff_var=


plt.figure(3);
mvalab.visusar(ima_coeff_var)

## Lee filter

This local coefficient is also used in a very famous filter for SAR images: Lee filter. 
The principle of the filter is to combine the pixel value $I_s$ (intensity value of pixel $s$) and the local mean $\hat{\mu}_{s}$ depending on the local coefficient of variation $\hat{\gamma}_s$ with the following formula :
$
  \hat{I}_s= \hat{\mu}_{s}+k_s (I_s-\hat{\mu}_{s})
$

and
$
  k_s=1- \frac{\gamma_S}{\hat{\gamma}_s}
$

$\gamma_S$ is the theoretical value of the coefficient of variation for a pure speckle ($\gamma_S=\frac{1}{\sqrt{L}}$ for a L-look intensity image).

Using the previous map, compute the resulting image with Lee filter. Comment the result and compare with a local mean. 

Warning : $k$ should be in $[0,1]$. 



In [0]:
# GIVEN THE ABOVE FORMULAS, DEFINE K TO FIND THE LEE FILTERED INTENSITY IMAGE
ks = 
mvalab.visusar(ks)
mvalab.visusar(npy.sqrt(ima_int))
image_lee_filtered = 
mvalab.visusar(npy.sqrt(npy.clip(image_lee_filtered,0,npy.max(image_lee_filtered))))



In [0]:
# REPEAT THE PROCESS WITH THE CROP FROM LELY
mvalab.visusar(numpy.abs(im_slc_senti_lely));

x = 470
y = 2230
pat_size = 512
im_slc_senti_lely_crop = im_slc_senti_lely[x : x+pat_size, y : y+pat_size]
mvalab.visusar(numpy.abs(im_slc_senti_lely_crop))
#plt.figure()
#%%
ima_int=numpy.multiply(im_slc_senti_lely_crop, numpy.conj(im_slc_senti_lely_crop))


size_window=11;
masque_loc=numpy.ones((size_window,size_window))/(size_window*size_window)
ima_intcarre=numpy.multiply(ima_int,ima_int)

ima_int_mean=signal.convolve2d(ima_int, masque_loc,mode='same')
plt.figure(1);
plt.rcParams['figure.figsize'] = [9, 9]
mvalab.visusar(numpy.sqrt(ima_int));

plt.figure(2);
mvalab.visusar(numpy.sqrt(ima_int_mean));

ima_int_mean_carre=signal.convolve2d(ima_intcarre, masque_loc,mode='same')
ima_variance=ima_int_mean_carre-numpy.multiply(ima_int_mean,ima_int_mean)
ima_coeff_var=numpy.divide(numpy.sqrt(ima_variance),ima_int_mean)


plt.figure(3);
mvalab.visusar(ima_coeff_var)

In [0]:
ks = 1 - (1 / ima_coeff_var)
mvalab.visusar(ks)
mvalab.visusar(npy.sqrt(ima_int))
image_lee_filtered = ima_int_mean + npy.multiply(ks,ima_int-ima_int_mean)
mvalab.visusar(npy.sqrt(npy.clip(image_lee_filtered,0,npy.max(image_lee_filtered))))

## Denoised image: SAR-CNN
The Lee filter presents some limits. More recent approaches to suppress noise rely on sofisticated algorithms. The foder  'pilelely/multitemp/' contains a series of images that have been denoised using the so called SAR-CNN, a deep learning algorithm. You can plot the image of Lely denoised using it and compare visually the result with the image filtered using the Lee filter.
  

In [0]:
image = 'Lely_denoised.IMF'
pageweb = 'https://perso.telecom-paristech.fr/dalsasso/TPSAR/pilelely/denoised_SARCNN/'
im_lely_denoised = mvalab.imz2mat(pageweb+image)
mvalab.visusar(im_lely_denoised[0])